In [5]:
!pip install matplotlib networkx torch gym numpy imageio seaborn procgen gym3 dataclasses 

In [6]:
!pip install stable_baselines3 


In [2]:
#import statements
import matplotlib.patches as patches
import networkx as nx
import torch.distributions
import torch
from procgen_wrappers import VecExtractDictObs, TransposeFrame, ScaledFloatFrame
import gym
import random
import numpy as np
#import helpers
import imageio
import matplotlib.pyplot as plt
import typing
import math

from procgen import ProcgenGym3Env
import struct
import typing
from typing import Tuple, Dict, Callable, List, Optional
from dataclasses import dataclass
#from src.policies_impala import ImpalaCNN

from gym3 import ToBaselinesVecEnv
import seaborn as sns
import random

%load_ext autoreload
%autoreload 2

In [22]:
# Dictionary of ordered layer names
ordered_layer_names = {
 1: 'conv_seqs.0',
 2: 'conv_seqs.0.conv',
 3: 'conv_seqs.0.max_pool2d',
 4: 'conv_seqs.0.res_block0',
 5: 'conv_seqs.0.res_block0.conv0',
 6: 'conv_seqs.0.res_block0.conv1',
 7: 'conv_seqs.0.res_block1',
 8: 'conv_seqs.0.res_block1.conv0',
 9: 'conv_seqs.0.res_block1.conv1',
 10: 'conv_seqs.1',
 11: 'conv_seqs.1.conv',
 12: 'conv_seqs.1.max_pool2d',
 13: 'conv_seqs.1.res_block0',
 14: 'conv_seqs.1.res_block0.conv0',
 15: 'conv_seqs.1.res_block0.conv1',
 16: 'conv_seqs.1.res_block1',
 17: 'conv_seqs.1.res_block1.conv0',
 18: 'conv_seqs.1.res_block1.conv1',
 19: 'conv_seqs.2',
 20: 'conv_seqs.2.conv',
 21: 'conv_seqs.2.max_pool2d',
 22: 'conv_seqs.2.res_block0',
 23: 'conv_seqs.2.res_block0.conv0',
 24: 'conv_seqs.2.res_block0.conv1',
 25: 'conv_seqs.2.res_block1',
 26: 'conv_seqs.2.res_block1.conv0',
 27: 'conv_seqs.2.res_block1.conv1',
 28: 'hidden_fc',
 29: 'logits_fc',
 30: 'value_fc'
}

# Extracting all the names into a list
layer_names = list(ordered_layer_names.values())
channels = {}
for layer_name in layer_names:
    if layer_name.startswith("conv_seqs.0"):
        channels[layer_name] = 16
    elif layer_name.startswith("conv"):
        channels[layer_name] = 32
    else:
        channels[layer_name] = 1

print(layer_names)


['conv_seqs.0', 'conv_seqs.0.conv', 'conv_seqs.0.max_pool2d', 'conv_seqs.0.res_block0', 'conv_seqs.0.res_block0.conv0', 'conv_seqs.0.res_block0.conv1', 'conv_seqs.0.res_block1', 'conv_seqs.0.res_block1.conv0', 'conv_seqs.0.res_block1.conv1', 'conv_seqs.1', 'conv_seqs.1.conv', 'conv_seqs.1.max_pool2d', 'conv_seqs.1.res_block0', 'conv_seqs.1.res_block0.conv0', 'conv_seqs.1.res_block0.conv1', 'conv_seqs.1.res_block1', 'conv_seqs.1.res_block1.conv0', 'conv_seqs.1.res_block1.conv1', 'conv_seqs.2', 'conv_seqs.2.conv', 'conv_seqs.2.max_pool2d', 'conv_seqs.2.res_block0', 'conv_seqs.2.res_block0.conv0', 'conv_seqs.2.res_block0.conv1', 'conv_seqs.2.res_block1', 'conv_seqs.2.res_block1.conv0', 'conv_seqs.2.res_block1.conv1', 'hidden_fc', 'logits_fc', 'value_fc']


In [23]:

def wrap_venv(venv) -> ToBaselinesVecEnv:
    "Wrap a vectorized env, making it compatible with the gym apis, transposing, scaling, etc."

    venv = ToBaselinesVecEnv(venv)  
    venv = VecExtractDictObs(venv, "rgb")

    venv = TransposeFrame(venv)
    venv = ScaledFloatFrame(venv)
    return venv  

def create_venv(
    num: int, start_level: int, num_levels: int, num_threads: int = 1, distribution_mode: str = "easy"
):
    """
    Create a wrapped venv. See https://github.com/openai/procgen#environment-options for params

    num=1 - The number of parallel environments to create in the vectorized env.

    num_levels=0 - The number of unique levels that can be generated. Set to 0 to use unlimited levels.

    start_level=0 - The lowest seed that will be used to generated levels. 'start_level' and 'num_levels' fully specify the set of possible levels.
    """
    venv = ProcgenGym3Env(
        num=num,
        env_name="heist",
        num_levels=num_levels,
        start_level=start_level,
        distribution_mode=distribution_mode,
        num_threads=num_threads,
        render_mode="rgb_array",
    )
    venv = wrap_venv(venv)
    return venv

In [24]:
from collections import defaultdict
from typing import List, Dict, Tuple
 
class Node:
    def __init__(self, name: str):
        self.name = name
        self.visited = False
        self.children = []
        self.parents = []


    def add_child(self, child_node):
        self.children.append(child_node)
        child_node.parents.append(self)

    def remove_child(self, child_node):
        if child_node in self.children:
            self.children.remove(child_node)
        if self in child_node.parents:
            child_node.parents.remove(self)

class Graph:
    def __init__(self):
        self.nodes = {}  # Maps node names to Node objects

    def add_node(self, name: str):
        if name not in self.nodes:
            self.nodes[name] = Node(name)
        return self.nodes[name]

    def add_edge(self, parent_name: str, child_name: str):
        parent_node = self.add_node(parent_name)
        child_node = self.add_node(child_name)
        parent_node.add_child(child_node)
    def add_edge_with_channels(self, parent_name: str, child_name: str):
        parent_channels = channels[parent_name]
        child_channels = channels[child_name]
        for parent_channel in range(parent_channels):
            for child_channel in range(child_channels):
                self.add_edge(parent_name+".channel"+str(parent_channel), child_name+".channel" + str(child_channel))

    def remove_edge(self, parent_name: str, child_name: str):
        try:
            parent_node = self.nodes[parent_name]
            child_node = self.nodes[child_name]
            parent_node.remove_child(child_node)
        except KeyError as e:
            print(f"Couldn't index in - are you sure this edge exists between {parent_name} and {child_name}?")
            raise e

    def display(self):
        for name, node in self.nodes.items():
            children_names = [child.name for child in node.children]
            parent_names = [parent.name for parent in node.parents]
            print(f'Node {name} has children: {children_names} and parents: {parent_names}')
def build_graph():
    graph = Graph()

    # Define the sequence names and their respective channels
    sequences = ['conv_seqs.0', 'conv_seqs.1', 'conv_seqs.2']
    last_seq_output = 'input'

    # Connect each sequence and define internal module connections
    for i, seq in enumerate(sequences):
        #add the skip connections
        graph.add_edge_with_channels(f'{seq}.max_pool2d', f'{seq}.res_block0')
        graph.add_edge_with_channels(f'{seq}.res_block0', f'{seq}.res_block1')  

        # Connect within ConvSequence
        graph.add_edge_with_channels(f'{seq}.conv', f'{seq}.max_pool2d')
        graph.add_edge_with_channels(f'{seq}.max_pool2d', f'{seq}.res_block0.conv0')
        graph.add_edge_with_channels(f'{seq}.res_block0.conv0', f'{seq}.res_block0.conv1')
        graph.add_edge_with_channels(f'{seq}.res_block0.conv1', f'{seq}.res_block0')

        graph.add_edge_with_channels(f'{seq}.res_block0', f'{seq}.res_block1.conv0')
        graph.add_edge_with_channels(f'{seq}.res_block1.conv0', f'{seq}.res_block1.conv1')
        graph.add_edge_with_channels(f'{seq}.res_block1.conv1', f'{seq}.res_block1')    
        graph.add_edge_with_channels(f'{seq}.res_block1',f'{seq}')

    # Connect hidden_fc to logits_fc and value_fc
    graph.add_edge_with_channels(f'{sequences[0]}', f'{sequences[1]}.conv')
    graph.add_edge_with_channels(f'{sequences[1]}', f'{sequences[2]}.conv')

    for i in range(32):
        graph.add_edge(f'{sequences[2]}.channel{i}', 'hidden_fc')

    ''' For now let's only remove the channel connection
    graph.add_node('hidden_fc')
    graph.add_node('logits_fc')
    graph.add_node('value_fc')
    graph.add_edge('hidden_fc', 'logits_fc')
    graph.add_edge('hidden_fc', 'value_fc')
    '''
    return graph

In [25]:
import helpers
model_path = "model_final.pt"
model = helpers.load_model(model_path=model_path)
graph = build_graph()
graph.display()

Node conv_seqs.0.max_pool2d.channel0 has children: ['conv_seqs.0.res_block0.channel0', 'conv_seqs.0.res_block0.channel1', 'conv_seqs.0.res_block0.channel2', 'conv_seqs.0.res_block0.channel3', 'conv_seqs.0.res_block0.channel4', 'conv_seqs.0.res_block0.channel5', 'conv_seqs.0.res_block0.channel6', 'conv_seqs.0.res_block0.channel7', 'conv_seqs.0.res_block0.channel8', 'conv_seqs.0.res_block0.channel9', 'conv_seqs.0.res_block0.channel10', 'conv_seqs.0.res_block0.channel11', 'conv_seqs.0.res_block0.channel12', 'conv_seqs.0.res_block0.channel13', 'conv_seqs.0.res_block0.channel14', 'conv_seqs.0.res_block0.channel15', 'conv_seqs.0.res_block0.conv0.channel0', 'conv_seqs.0.res_block0.conv0.channel1', 'conv_seqs.0.res_block0.conv0.channel2', 'conv_seqs.0.res_block0.conv0.channel3', 'conv_seqs.0.res_block0.conv0.channel4', 'conv_seqs.0.res_block0.conv0.channel5', 'conv_seqs.0.res_block0.conv0.channel6', 'conv_seqs.0.res_block0.conv0.channel7', 'conv_seqs.0.res_block0.conv0.channel8', 'conv_seqs.0.

In [26]:
import torch
from stable_baselines3 import PPO
from stable_baselines3.common.callbacks import BaseCallback
import numpy as np

def format_layer_name(layer_name):
    return layer_name.replace('.', '_')

class ModelActivations:
    def __init__(self, model):
        self.activations = {}
        self.model = model
        self.hooks = []  # To keep track of hooks
        self.layer_paths = layer_names

    def clear_hooks(self):
        # Remove all previously registered hooks
        for hook in self.hooks:
            hook.remove()
        self.hooks = []
        self.activations = {}

    def get_activation(self, name):
        def hook(model, input, output):
            processed_output = []
            for item in output:
                if isinstance(item, torch.Tensor):
                    processed_output.append(item.detach())
                elif isinstance(item, torch.distributions.Categorical):
                    processed_output.append(item.logits.detach())
                else:
                    processed_output.append(item)
            self.activations[name] = tuple(processed_output)
        return hook

    def register_hook_by_path(self, path, name):
        elements = path.split('.')
        model = self.model
        for i, element in enumerate(elements):
            if '[' in element:
                base, index = element.replace(']', '').split('[')
                index = int(index)
                model = getattr(model, base)[index]
            else:
                model = getattr(model, element)
            if i == len(elements) - 1:
                hook = model.register_forward_hook(self.get_activation(name))
                self.hooks.append(hook)  # Keep track of the hook

    def run_with_cache(self, input):
        self.clear_hooks()  # Clear any existing hooks
        self.activations = {}  # Reset activations

        # Handle edge case: input is not a tensor
        if not isinstance(input, torch.Tensor):
            input = torch.tensor(input, dtype=torch.float32)


        # Check the shape of the input and reshape if necessary
        if input.shape == torch.Size([1, 3, 64, 64]):
            input = input.squeeze(0)  # Remove the batch dimension
        if input.shape == torch.Size([3, 64, 64]):
            input = input.permute(1, 2, 0)  # Switch dimensions to (64, 64, 3)


        # Handle edge case: empty layer_paths
        if not self.layer_paths:
            output = self.model(input)
            return output, self.activations

        # Register hooks for each layer path
        for path in self.layer_paths:
            try:
                self.register_hook_by_path(path, path.replace('.', '_'))
            except AttributeError:
                print(f"Warning: Layer '{path}' not found in the model. Skipping hook registration.")

        # Add batch dimension if missing
        if input.dim() == 3:
            input = input.unsqueeze(0)

        # Run the model with the registered hooks
        output = self.model(input)

        return output, self.activations
    

    def register_hook_by_path_variant(self, path, name, corrupt_cache, layer_name_channels, ablate):
        elements = path.split('.')
        model = self.model
        for i, element in enumerate(elements):
            if '[' in element:
                base, index = element.replace(']', '').split('[')
                index = int(index)
                if hasattr(model, base) and index < len(getattr(model, base)):
                    model = getattr(model, base)[index]
                else:
                    print(f"Attribute '{base}' or index '{index}' does not exist in the model.")
                    return
            else:
                if hasattr(model, element):
                    model = getattr(model, element)
                else:
                    print(f"Attribute '{element}' does not exist in the model.")
                    return
            if i == len(elements) - 1:
                hook = model.register_forward_hook(self.get_activation_variant(name, corrupt_cache, layer_name_channels, ablate))
                self.hooks.append(hook)
    def get_activation_variant(self, name, corrupt_cache={}, layer_name_channels={}, ablate=False):
        layer_name_channel_copy = {}
        for key, value in layer_name_channels.items():
            layer_name_channel_copy[key.replace('.','_')] = value
        def hook(model, input, output):
            self.activations[name] = output.detach()
            
            if name in layer_name_channel_copy:
                if ablate:
                    for channel in layer_name_channel_copy[name]:
                        output[:, channel, :, :] = 0
               
                elif name.replace('.','_') in corrupt_cache:
                    
                    #print("the dimension of the corrupt_cache", corrupt_cache[name][0].unsqueeze(0).shape)
                    #print("patching in", name)
                    corrupted_output = corrupt_cache[name][0].unsqueeze(0)
                    if corrupted_output.shape == output.shape:
                        #print("the dimension of the output", output.shape, name)
                        for channel in layer_name_channel_copy[name]:
                            output[:, channel, :, :] = corrupted_output[:, channel, :, :]
            return output
        return hook



    def patch_activations_variant(self, input, corrupt_cache={}, to_change_layer_name=[], ablate=False):
        '''
        layer_name_channels = {}
        layer_names =['conv_seqs.0', 'conv_seqs.0.conv', 'conv_seqs.0.max_pool2d', 
                      'conv_seqs.0.res_block0', 'conv_seqs.0.res_block0.conv0', 'conv_seqs.0.res_block0.conv1', 'conv_seqs.0.res_block1']

        
        #This is what corrupt cache looks like

        #(['conv_seqs_0_conv', 'conv_seqs_0_max_pool2d', 'conv_seqs_0_res_block0_conv0', 'conv_seqs_0_res_block0_conv1', 'conv_seqs_0_res_block0', 'conv_seqs_0_res_block1_conv0', 'conv_seqs_0_res_block1_conv1', 'conv_seqs_0_res_block1', 'conv_seqs_0', 'conv_seqs_1_conv', 'conv_seqs_1_max_pool2d', 'conv_seqs_1_res_block0_conv0', 'conv_seqs_1_res_block0_conv1', 'conv_seqs_1_res_block0', 'conv_seqs_1_res_block1_conv0', 'conv_seqs_1_res_block1_conv1', 'conv_seqs_1_res_block1', 'conv_seqs_1', 'conv_seqs_2_conv', 'conv_seqs_2_max_pool2d', 'conv_seqs_2_res_block0_conv0', 'conv_seqs_2_res_block0_conv1', 'conv_seqs_2_res_block0',
         # 'conv_seqs_2_res_block1_conv0', 'conv_seqs_2_res_block1_conv1', 'conv_seqs_2_res_block1', 
          #'conv_seqs_2', 'hidden_fc', 'logits_fc', 'value_fc'])
        for layer_name in layer_names:
            layer_name_channels[layer_name] = [0]
        '''
        layer_name_channels = {}
        for name in to_change_layer_name:
            if ".channel" in name:
                base_name, channel = name.rsplit(".channel", 1)
                channel = int(channel)
                if base_name in layer_name_channels:
                    layer_name_channels[base_name].append(channel)
                else:
                    layer_name_channels[base_name] = [channel]

                
        #print("layer_name_channels", layer_name_channels)
    

        # Register hooks with modified behavior
        for layer_path, channels in layer_name_channels.items():
            self.register_hook_by_path_variant(layer_path, layer_path.replace('.', '_'), corrupt_cache, layer_name_channels, ablate)
            

        # Handle the input tensor shape and type
        if not isinstance(input, torch.Tensor):
            input = torch.tensor(input, dtype=torch.float32)
        if input.shape == torch.Size([1, 3, 64, 64]):
            input = input.squeeze(0)
        if input.shape == torch.Size([3, 64, 64]):
            input = input.permute(1, 2, 0)
        if input.dim() == 3:
            input = input.unsqueeze(0)

        output = self.model(input)

        self.clear_hooks()

        return output, self.activations




In [27]:
class RLPolicyExperiment():
    """
    A class to manage an experiment that adjusts and analyzes the components of an RL policy
    network dynamically during training, akin to the TLACDCExperiment for neural networks.
    """

    def __init__(self, model, threshold,graph,input,corrupt_input, ablate):
        self.model = model
        self.model_activations = ModelActivations(model)
        #this should be input dataset
        self.input = input
        self.corrupt_input = corrupt_input
        self.threshold = threshold
        # Node definitions are based on the provided structure
        self.graph = graph
        self.removed_nodes = []
        self.removed_edges = []
        self.ablate = ablate
        self.mean_kl_divergences = 0

        

    def reverse_topologically_sort_corr(self):
        #sorts the graph in reverse topological order
        order = []
        # Set all nodes as unvisited
        for node in self.graph.nodes.values():
            node.visited = False

        # Helper function to perform DFS
        def dfs(node):
            node.visited = True
            for child in node.children:
                if not child.visited:
                    dfs(child)
            # Prepend node to maintain reverse order
            order.insert(0, node.name)

        # Perform DFS from each unvisited node
        for node in self.graph.nodes.values():
            if not node.visited:
                dfs(node)
        return order

            
    def _on_step(self):
        kl_divergences = []
        clean_logits, _ = self.model_activations.run_with_cache(self.input) # Get original logits with normal activations
        self.model_activations.clear_hooks()
        
        _, corrupt_cache = self.model_activations.run_with_cache(self.corrupt_input) # Get original logits with normal activations
        self.model_activations.clear_hooks()

        
        order = self.reverse_topologically_sort_corr()
        order.reverse()
        print(order)

        for node in order:

            current_node = self.graph.nodes[node]
            #print("here is the current node", current_node)
            
            # Simulate zero activation for the first node and get the kl divergence
            for parent_node in current_node.parents:
                #to_patch_nodes = self.removed_nodes.copy()
                to_patch_nodes = []
                if parent_node.name not in to_patch_nodes:
                    to_patch_nodes.append(parent_node.name)
  
                if self.ablate:
                    modified_logits, _ = self.model_activations.patch_activations_variant(self.input, corrupt_cache =corrupt_cache,to_change_layer_name=to_patch_nodes,ablate =True)
                else:
                    modified_logits, _ = self.model_activations.patch_activations_variant(input =self.input, corrupt_cache=corrupt_cache,to_change_layer_name=to_patch_nodes, ablate= False)
                self.model_activations.clear_hooks()
                
                prob1 = torch.softmax(clean_logits[0].logits, dim=1)
                prob2 = torch.softmax(modified_logits[0].logits, dim=1)
                kl_div = torch.nn.functional.kl_div(torch.log(prob1), prob2, reduction='batchmean')
                print("the kl divergence is", kl_div)
                
                kl_divergences.append(kl_div)
                

                remove = kl_div < self.threshold 

                if remove:
                    print("permanently removing an edge in the graph", parent_node.name, current_node.name)
                    self.graph.remove_edge(parent_node.name,current_node.name)
                    self.removed_edges.append((parent_node,current_node))
                    if parent_node.name not in self.removed_nodes:
                        self.removed_nodes.append(parent_node.name)
        self.mean_kl_divergences =sum(kl_divergences) / len(kl_divergences)
       
      

In [ ]:
import heist
start_level = random.randint(1, 10000)
venv = create_venv(num=1, num_levels=1, start_level=start_level)
state = heist.state_from_venv(venv, 0)
corrupt_input = venv.reset()    #the input with the blue key is the corrupt input
corrupt_input = helpers.observation_to_rgb(corrupt_input)
state_values = state.state_vals

for ents in state_values["ents"]:
    if ents["image_type"].val== 9:
        gem_x = ents["x"].val 
        gem_y = ents["y"].val 

state.remove_gem()

state_bytes = state.state_bytes
if state_bytes is not None:
    venv.env.callmethod("set_state", [state_bytes])
    input = venv.reset()
    input = helpers.observation_to_rgb(input)


experiment = RLPolicyExperiment(model,0.0001,build_graph(),input,corrupt_input,ablate=False)
experiment._on_step()
#print(experiment.graph.display())
print("the mean of the kl divergences are" , experiment.mean_kl_divergences)


['hidden_fc', 'conv_seqs.2.channel0', 'conv_seqs.2.channel1', 'conv_seqs.2.channel2', 'conv_seqs.2.channel3', 'conv_seqs.2.channel4', 'conv_seqs.2.channel5', 'conv_seqs.2.channel6', 'conv_seqs.2.channel7', 'conv_seqs.2.channel8', 'conv_seqs.2.channel9', 'conv_seqs.2.channel10', 'conv_seqs.2.channel11', 'conv_seqs.2.channel12', 'conv_seqs.2.channel13', 'conv_seqs.2.channel14', 'conv_seqs.2.channel15', 'conv_seqs.2.channel16', 'conv_seqs.2.channel17', 'conv_seqs.2.channel18', 'conv_seqs.2.channel19', 'conv_seqs.2.channel20', 'conv_seqs.2.channel21', 'conv_seqs.2.channel22', 'conv_seqs.2.channel23', 'conv_seqs.2.channel24', 'conv_seqs.2.channel25', 'conv_seqs.2.channel26', 'conv_seqs.2.channel27', 'conv_seqs.2.channel28', 'conv_seqs.2.channel29', 'conv_seqs.2.channel30', 'conv_seqs.2.channel31', 'conv_seqs.2.res_block1.channel0', 'conv_seqs.2.res_block1.channel1', 'conv_seqs.2.res_block1.channel2', 'conv_seqs.2.res_block1.channel3', 'conv_seqs.2.res_block1.channel4', 'conv_seqs.2.res_bloc

In [21]:
for node1, node2 in experiment.removed_edges:
    print(node1.name, node2.name)

conv_seqs.2.channel0 hidden_fc
conv_seqs.2.channel2 hidden_fc
conv_seqs.2.channel4 hidden_fc
conv_seqs.2.channel6 hidden_fc
conv_seqs.2.channel9 hidden_fc
conv_seqs.2.channel12 hidden_fc
conv_seqs.2.channel14 hidden_fc
conv_seqs.2.channel16 hidden_fc
conv_seqs.2.channel18 hidden_fc
conv_seqs.2.channel20 hidden_fc
conv_seqs.2.channel22 hidden_fc
conv_seqs.2.channel25 hidden_fc
conv_seqs.2.channel28 hidden_fc
conv_seqs.2.channel30 hidden_fc
conv_seqs.2.res_block1.channel0 conv_seqs.2.channel0
conv_seqs.2.res_block1.channel2 conv_seqs.2.channel0
conv_seqs.2.res_block1.channel4 conv_seqs.2.channel0
conv_seqs.2.res_block1.channel6 conv_seqs.2.channel0
conv_seqs.2.res_block1.channel9 conv_seqs.2.channel0
conv_seqs.2.res_block1.channel12 conv_seqs.2.channel0
conv_seqs.2.res_block1.channel14 conv_seqs.2.channel0
conv_seqs.2.res_block1.channel16 conv_seqs.2.channel0
conv_seqs.2.res_block1.channel18 conv_seqs.2.channel0
conv_seqs.2.res_block1.channel20 conv_seqs.2.channel0
conv_seqs.2.res_block1